In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:85% !important; }</style>"))
debug_mode=1 # if not in debug mode, please set debug_mode=0, find more info about debug mode in test run 9 maybe?
%load_ext autoreload
%autoreload 2
%matplotlib inline

In [2]:
import os
os.environ['SNORKELDB'] = "postgresql:///abstractnet2konset"
print(os.environ['SNORKELDB'])
from snorkel import SnorkelSession
from snorkel.parser import TSVDocPreprocessor
session = SnorkelSession()

## Here, we just set the upperbound for how many documents we'll process!
n_docs = 10000
# doc_preprocessor = TSVDocPreprocessor('data/annotations_label-level_all-to-date-2018-4-25-WithTitle_full_abstract_punc_concatenated.csv', encoding="utf-8",max_docs=n_docs)
doc_preprocessor = TSVDocPreprocessor('data/larger-slim-con-2k', encoding="utf-8",max_docs=n_docs)


from snorkel.parser.spacy_parser import Spacy
from snorkel.parser import CorpusParser

# corpus_parser = CorpusParser(parser=Spacy())
# %time corpus_parser.apply(doc_preprocessor, count=n_docs)# ,parallelism=5)

from snorkel.models import Document, Sentence  # defined in context.py file
print("Documents:", session.query(Document).count())

postgresql:///abstractnet2konset
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True


/anaconda3/lib/python3.6/site-packages/psycopg2/__init__.py:144: UserWarning: The psycopg2 wheel package will be renamed from release 2.8; in order to keep installing from binary please use "pip install psycopg2-binary" instead. For details see: <http://initd.org/psycopg/docs/install.html#binary-install-from-pypi>.
  """)


Documents: 9498


## I. Background
### A. Preprocessing the Corpus and Save to the Database (Done)

The corpus could be downloaded [here](https://github.com/xeniaqian94/snorkel/blob/master/abstractnet/testrun/data/slim-slim-top-tier-citation).

### B. Connect to the Database and retrieve Document

Recall the Document/Sentence/Candidate hierarchy in the guideline. We also divide the whole document set into buckets of each 100 documents.

In [3]:
from snorkel import SnorkelSession
from snorkel.parser.spacy_parser import Spacy
from snorkel.parser import CorpusParser
from snorkel.models import Document, Sentence
from collections import defaultdict
import numpy as np

session = SnorkelSession()
docs = session.query(Document).all()
sents = session.query(Sentence).all()  # get all sentences from snorkel.db

docs_per_bucket=260
sents_split=defaultdict(lambda:[])
for ind, doc in enumerate(docs):
    bucket=int(ind/docs_per_bucket)
    for s in doc.sentences:
        sents_split[bucket]+=[s]
print("Number of buckets", len(sents_split))

Number of buckets 37


### C. From Documents to Extract Candidates

Here we extract the candidates (i.e. unigrams) from one of the document bucket, which has approximately 100 documents. Here we use <b>Bucket 0</b>. So it is our train bucket to learn the generative model from LFs. Later we will use <b>Bucket 1</b> as the development bucket, to draw visualizations and provide feedbacks. 

In [4]:
from snorkel.models import candidate_subclass
from snorkel.candidates import Ngrams, CandidateExtractor
from snorkel.matchers import *
import datetime

from IPython.display import Markdown, display
def printmd(string):
    display(Markdown(string))

Unigram = candidate_subclass('Unigram', ['unigram_cue'],values=['PP','MN','NULL'])
ngrams = Ngrams(n_max=1) 
ngram_matcher=NgramMatcher()
unigram_segment_extractor=CandidateExtractor(Unigram,[ngrams],[ngram_matcher])

train_bucket=0
# %time unigram_segment_extractor.apply(sents_split[train_bucket], split=train_bucket)
unigram_segments=session.query(Unigram).filter(Unigram.split == train_bucket).all()
print("Number of Candidates/Unigrams",len(unigram_segments))

Number of Candidates/Unigrams 49204


## II. Labeling Functions


In [5]:
from snorkel.lf_helpers import *
from snorkel.annotations import LabelAnnotator

# from LF.util_common_default_categorical import purpose_LFs,mechanism_LFs,null_LFs
from LF.util_common_default_categorical_onset_1026 import * 
# purpose_LFs,mechanism_LFs,null_LFs
print("total LF count", len(purpose_LFs+mechanism_LFs+null_LFs), "unique count",len(set(purpose_LFs+mechanism_LFs+null_LFs)),"purpose_LFs",len(purpose_LFs),"mechanism_LFs",len(mechanism_LFs))
print("\n\npurpose_LFs\n",[lf.__name__ for lf in purpose_LFs])
print("\n\nmechanism_LFs\n",[lf.__name__ for lf in mechanism_LFs])
print("\n\nnull_LFs\n",[lf.__name__ for lf in null_LFs])

/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


total LF count 32 unique count 32 purpose_LFs 17 mechanism_LFs 15


purpose_LFs
 ['purpose_for_clause', 'purpose_to_verb', 'purpose_but_followed_next_sentence_we', 'purpose_our_followed_by_goal', 'purpose_the_followed_by_goal', 'purpose_we_study', 'purpose_however_follow_by_comma', 'purpose_we_follow_by_consider', 'purpose_we_follow_by_examine', 'purpose_will_follow_by_allow', 'purpose_that_follow_by_allows', 'purpose_will_follow_by_enable', 'purpose_starting_what', 'purpose_starting_how', 'purpose_starting_although', 'purpose_this_paper_investigates', 'purpose_we_investigate']


mechanism_LFs
 ['mechanism_we_propose', 'mechanism_we_develop', 'mechanism_we_design', 'mechanism_we_model', 'mechanism_we_modeled', 'mechanism_we_introduce', 'mechanism_we_introduced', 'mechanism_we_present', 'mechanism_our_followed_by_work', 'mechanism_our_followed_by_approach', 'mechanism_we_followed_by_extend', 'mechanism_our_followed_by_system', 'mechanism_by_adv_doing', 'mechanism_this_paper', 'mechanism

### Test playground

In [25]:
# print(unigram_segments[0].get_parent().dict__[])

count=0
for idx,segment in enumerate(unigram_segments):
#     if abs(idx-18393)==2:
#     if get_candidate_text(segment).lower()=="by":
    if False:
#     if purpose_to_verb(segment)!=0:
        
#     if "we study" in " ".join(get_surrounding_words(segment,0,including_itself=True)):
#     if mechanism_LFs[-2](segment)!=0:  # operationalization
#         print(mechanism_LFs[-3](segment))
    
#         c=segment
#         to_idx=get_candidate_idx(c)
#         print(to_idx)
#         dep_parents_whole_sent=get_surrounding_dep_parents(c,0,including_itself=True)
#         pos_tags_whole_sent=get_surrounding_tags(c,0,including_itself=True)
#         for idx in range(to_idx+1,len(dep_parents_whole_sent)):
#             if dep_parents_whole_sent[idx]==(to_idx+1):
#                 print(pos_tags_whole_sent[idx])
#                 if pos_tags_whole_sent[idx]=="VBG":
#                     print("MECHANISM_LABEL")

        
        print(idx,segment.get_parent().__dict__['text'])
        print(get_candidate_text(segment))
        print(get_candidate_idx(segment))
        print(get_surrounding_dep_parents(segment,0,including_itself=True))
        print(get_surrounding_tags(segment,0,including_itself=True))
        sentence=segment.get_parent()
        doc_sentences=sentence.get_parent().sentences
        sent_idx=doc_sentences.index(sentence)
        if sent_idx==len(doc_sentences)-1:
            continue
        next_sent_token=doc_sentences[sent_idx+1].__dict__['text'].lower()
        print(next_sent_token)
        print("")
        if count>30:
            break
        count+=1
    
input()
purpose_LFs=[]
from LF.util_common_default_categorical_1022 import purpose_LFs,mechanism_LFs

for i in range(695,725):
    print(unigram_segments[i])
    print(unigram_segments[i].get_parent().__dict__['text'])
    print(purpose_LFs[-1](unigram_segments[i]))
#     print(purpose_LFs[-1].__name__)
    print()
    
    
# print(unigram_segments[165],)

segment=unigram_segments[165]
# print((segment.get_contexts()[0].__dict__))
docid=segment.get_parent().get_parent().name
print(segment)
print("sent __dict__",segment.get_parent().__dict__)
print("sent pos in doc??", segment.get_parent().position)
# print("sent pos in doc??", segment.get_parent().get_parent().sentences.index(segment.get_parent()))

print(docid)

# print(segment.get_parent().get_parent().__dict__)
print(segment.get_parent().text[segment.unigram_cue.char_start:segment.unigram_cue.char_end+1])

unigram_psn=segment.unigram_cue.get_word_start()
print("unigram position?? ",unigram_psn)#.__dict__['words'])

its_pos_tag=segment.get_parent().__dict__['pos_tags'][unigram_psn]
print("its_pos_tag",its_pos_tag,"\n")

KeyboardInterrupt: 

## VI. Development Sandbox
### A. Writing New Labeling Functions

We will name them as `new_LFs`.

In [6]:
#
# PLACE YOUR LFs HERE
#
new_LFs=[]

### B. Applying Labeling Functions

In here we define two functions: (1) applying LFs to get an annotation matrix; (2) use the annotation matrix to learn a generative model.

In [6]:
from snorkel.learning import GenerativeModel
from util import get_candidate_text
import matplotlib.pyplot as plt
import datetime

def get_L_train(LFs,parallelism=1,split=0):
    L_train=None
    labeler=None
    np.random.seed(1701)
    labeler = LabelAnnotator(lfs=LFs)
    print(datetime.datetime.now())
    L_train = labeler.apply(split=split,parallelism=parallelism)# ,cids_query=session.query(Candidate.id).filter(Candidate.get_parent().id %10==1))
    print(datetime.datetime.now())
    print(type(L_train))
    print(L_train.shape)
    printmd("**Total non_overlapping_coverage on L_train (percentage of labelled over all)**  "+str(L_train.non_overlapping_coverage()))
    return L_train

def get_train_marginals(L_train,step_size_nominator=0.1,epochs=100,lf_propensity=True,threads=1,class_prior=False,decay=1.0,reg_param=1e-6):
    try:
        gen_model=None
        print(datetime.datetime.now())
        gen_model = GenerativeModel(lf_propensity=lf_propensity,class_prior=class_prior)
        gen_model.train(L_train, cardinality=3, epochs=epochs, decay=decay,step_size=step_size_nominator/1e2,reg_param=reg_param,verbose=False,threads=threads)
        print("training finished ")
        print(datetime.datetime.now())
        print("Finished training generative model, now checking performance against development set labels...")
        print("Calculating marginals!")
        train_marginals = gen_model.marginals(L_train)  # the marginal probability of each candidate being True
        print("no exception")
        print(datetime.datetime.now())
        return gen_model,train_marginals
    except:
        print("exception! ")
        return gen_model,train_marginals


In [12]:
L_train=get_L_train(purpose_LFs+mechanism_LFs+null_LFs+new_LFs)
print(L_train.shape)

snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
2018-11-13 01:16:42.124923
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
cids_count 49204
key_group 0
Clearing existing...
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
clearing..
Running UDF...
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
[========================================] 100%

2018-11-13 01:20:38.419167
<class 'snorkel.annotations.csr_LabelMatrix'>
(49204, 32)


**Total non_overlapping_coverage on L_train (percentage of labelled over all)**  0.013901308836679945

(49204, 32)


In [29]:
import pandas as pd 
pd.set_option('display.max_rows', 500)

df=L_train.lf_stats(session)
df['Conflict_Coverage_ratio'] = df['Conflicts']/df['Coverage']

df_ratio_added=df.sort_values(by=['Conflict_Coverage_ratio'],ascending=False)

# df_ratio_added[df_ratio_added.index.str.contains("we_similar")]
print(df_ratio_added.sum(axis=0))
print(df_ratio_added)

j                          496.000000
Coverage                     0.013901
Overlaps                     0.000000
Conflicts                    0.000000
Conflict_Coverage_ratio      0.000000
dtype: float64
                                        j  Coverage  Overlaps  Conflicts  \
purpose_for_clause                      0  0.001158       0.0        0.0   
purpose_to_verb                         1  0.003150       0.0        0.0   
mechanism_this_paper                   30  0.000264       0.0        0.0   
mechanism_by_adv_doing                 29  0.002012       0.0        0.0   
mechanism_our_followed_by_system       28  0.000020       0.0        0.0   
mechanism_we_followed_by_extend        27  0.000020       0.0        0.0   
mechanism_our_followed_by_approach     26  0.000244       0.0        0.0   
mechanism_our_followed_by_work         25  0.000122       0.0        0.0   
mechanism_we_present                   24  0.000467       0.0        0.0   
mechanism_we_introduce             

In [ ]:
for reg_param in [1e-3]:#,1e-6]: #[1e-3, 1e-6]:
    for decay in [0.95]: #[1.0,0.95]:
        for step_size_nominator in [0.01,0.001]: # [0.01, 0.1, 1]:
            for epochs in [2,3,4,5,7]:#,30,50,100,200,500]:
                for lf_propensity in [False]:
                    
                    print("grid search with L_train","step_size_nominator",step_size_nominator,"epochs",epochs,"decay",decay,"reg_param",reg_param,"lf_propensity",lf_propensity)
                    gen_model,train_marginals=get_train_marginals(L_train,threads=18,lf_propensity=lf_propensity,step_size_nominator=step_size_nominator,epochs=epochs,decay=decay,reg_param=reg_param)
                    assert np.all(train_marginals.sum(axis=1) - np.ones(train_marginals.shape[0]) < 1e-10)

                    winHighlight=train_marginals.argmax(axis=1)
                    print("PP",(winHighlight==0).sum())
                    print("MN",(winHighlight==1).sum())
                    print("NULL",(winHighlight==2).sum())

                    # Amendment!!! winning highligh with default as NULL (the last occurence of largest value)
                    train_marginals_reverse = train_marginals[:,::-1]
                    winHighlight = train_marginals.shape[1] - np.argmax(train_marginals_reverse,axis=1) - 1
                    print("amend PP",(winHighlight==0).sum())
                    print("amend MN",(winHighlight==1).sum())
                    print("amend NULL",(winHighlight==2).sum())


### C. Learning the Generative Model

In [7]:
reg_param=1e-3
decay=0.95
step_size_nominator=0.01
epochs=100
lf_propensity=False
                        
print("train starts here", datetime.datetime.now())
gen_model,train_marginals=get_train_marginals(L_train,threads=18,step_size_nominator=step_size_nominator,lf_propensity=lf_propensity,epochs=epochs,decay=decay,reg_param=reg_param)
assert np.all(train_marginals.sum(axis=1) - np.ones(train_marginals.shape[0]) < 1e-10)

winHighlight=train_marginals.argmax(axis=1)
print("PP",(winHighlight==0).sum())
print("MN",(winHighlight==1).sum())
print("NULL",(winHighlight==2).sum())

# Amendment!!! winning highligh with default as NULL (the last occurence of largest value)
train_marginals_reverse = train_marginals[:,::-1]
winHighlight = train_marginals.shape[1] - np.argmax(train_marginals_reverse,axis=1) - 1
print("amend PP",(winHighlight==0).sum())
print("amend MN",(winHighlight==1).sum())
print("amend NULL",(winHighlight==2).sum())

train starts here 2018-11-13 17:08:44.868613


NameError: name 'L_train' is not defined

In [27]:
pair_list=list(zip(unigram_segments,list(train_marginals[:,0].reshape(-1))))

pair_list.sort(key = lambda t: t[1],reverse=True)

def get_candidate_text(candidate):
    cue=candidate.get_contexts()[0]
    return cue.sentence.text[cue.char_start:cue.char_end+1]

top_cutoff=124
print("top purpose words \n\n")
print("\n\n".join([str(ind)+"\tWord\t"+get_candidate_text(pair[0])+"\n"+"Sentence\t"+str(pair[0].get_parent().text)+"\t"+str(pair[1]) for ind,pair in enumerate(pair_list[:top_cutoff])]))

pair_list=list(zip(unigram_segments,list(train_marginals[:,1].reshape(-1))))

pair_list.sort(key = lambda t: t[1],reverse=True)

top_cutoff=120
print("top mechanism words \n\n")
print("\n\n".join([str(ind)+"\tWord\t"+get_candidate_text(pair[0])+"\n"+"Sentence\t"+str(pair[0].get_parent().text)+"\t"+str(pair[1]) for ind,pair in enumerate(pair_list[:top_cutoff])]))



top purpose words 


0	Word	What
Sentence	What were the most important factors in determining the classification outcome ?	0.5015485252471279

1	Word	What
Sentence	What can we say about these marked nodes ?	0.5015485252471279

2	Word	What
Sentence	What do graphs look like ?	0.5015485252471279

3	Word	What
Sentence	What do real communities in social networks look like ?	0.5015485252471279

4	Word	How
Sentence	How do individuals perceive algorithmic vs. group-made decisions ?	0.5010779639593546

5	Word	How
Sentence	How effective are call and SMS logs in modeling tie strength ?	0.5010779639593546

6	Word	How
Sentence	How do participants spend their time preparing, working face-to- face, and following through these brief encounters ?	0.5010779639593546

7	Word	How
Sentence	How can we automatically determine how many, if any groups they form as well as find simple paths that connect the nodes in each group ?	0.5010779639593546

8	Word	How
Sentence	How do they evolve over time ?	0.5010779639

0	Word	we
Sentence	In the present work, we develop a method to extract the stereotypes of Twitter users.	0.5009646797234981

1	Word	we
Sentence	In this work, we develop a more robust framework that addresses this novel problem.	0.5009646797234981

2	Word	We
Sentence	We developed three such privacy nudges on Facebook.	0.5009646797234981

3	Word	we
Sentence	To this end, we develop a logically motivated theory of parametric polymorphism, reminiscent of the Girard-Reynolds polymorphic -calculus, but casted in the setting of concurrent processes.	0.5009646797234981

4	Word	we
Sentence	In particular, we develop an efficient proximal Newton method which minimizes per-iteration cost with a coordinate descent active set approach and fast numerical solutions to the Lyapunov equations. Experimentally we demonstrate the appeal of this approach on synthetic examples and real power networks significantly larger than those previously considered in the literature.
	0.5009646797234981

5	Word	we
Senten

### D. Visualize generative labels on this train set, then on the dev set

In [8]:
from collections import defaultdict
import matplotlib.pyplot as plt
import seaborn as sns
import os 
import pandas as pd

def pad_reshape(A,width,isFloat=False):
    B=np.empty([1,int(A.shape[1]/width+1)*width],dtype=object)
    if isFloat:
        B=np.zeros([1,int(A.shape[1]/width+1)*width])
        B[:,:A.shape[1]]=A
    else:
        B[:,:A.shape[1]]=A
        B[:,A.shape[1]:]=""
    return B.reshape(-1,width)
 

def create_new_score_array(smooth_window,score_array,word_array):
    new_score_array=np.zeros(score_array.shape)
    half_window=int(smooth_window/2)
    punctuation=[",","."]
    for i in range(score_array.shape[1]):
        sub_score_array=score_array[0,max(0,i-half_window):i+half_window+1]
        sub_word_array=word_array[0,max(0,i-half_window):i+half_window+1]

        mid_pos=half_window

        left_pos=mid_pos
        right_pos=mid_pos
#         print(sub_word_array[left_pos],type(sub_word_array[left_pos]))
        while left_pos>0 and str(sub_word_array[left_pos-1][0]) not in punctuation:
            left_pos-=1
        while right_pos<len(sub_word_array):
            right_pos+=1
            if str(sub_word_array[right_pos-1][0]) in punctuation:
                break
        new_score_array[0,i]=np.mean(sub_score_array[left_pos:right_pos])
    return new_score_array


In [9]:
def get_candidate_text(segment):
    return segment.get_parent().text[segment.get_contexts()[0].char_start:segment.get_contexts()[0].char_end+1]

def write_csv_gen_label(unigram_segments,train_marginals,csv_path,smooth_window=0):
    
#     pair_list=list(zip(unigram_segments,train_marginals))
#     new_unigram_segments=[]
#     new_train_marginals=[]
#     doc_dict=defaultdict(lambda:[])
#     for ind,pair in enumerate(pair_list):
#         if ind%10000==0:
#             print(ind)
#         docid=pair[0].get_parent().get_parent().name
#         doc_dict[docid]+=[pair]

#     for docid in doc_dict:
#         doc_dict[docid]=sorted(doc_dict[docid], key=lambda pair: (pair[0].get_parent().position, pair[0].get_contexts()[0].get_word_start()))

#         ordered_word_score_list=[(pair[0].get_parent().text[pair[0].unigram_cue.char_start:pair[0].unigram_cue.char_end+1], pair[1]) for pair in doc_dict[docid]]
#         df=pd.DataFrame.from_records(ordered_word_score_list,columns=['word','score'])
#         score_array=np.asarray(df[['score']]).reshape(1,-1)
#         new_train_marginals_array=np.zeros([len(doc_dict[docid]),len(score_array[0,0])])
#         word_array=np.asarray(df[['word']]).reshape(1,-1)
#         for i in range(len(score_array[0,0])):
            
#             segment_score_array=np.asarray([score_array[0,segment_idx][i] for segment_idx in range(len(doc_dict[docid]))]).reshape(-1)
# #             print(i,segment_score_array.shape)
# #             print(segment_score_array)  # 1 * num_token

#             new_train_marginals_array[:,i]=segment_score_array
            
#         for ind, pair in enumerate(doc_dict[docid]):
#             new_unigram_segments+=[pair[0]]
#             new_train_marginals+=[new_train_marginals_array[ind]]
      
#     unigram_segments=new_unigram_segments
#     train_marginals=new_train_marginals
        
    aggregated_doc=defaultdict(lambda:[])
    aggregated_sent=defaultdict(lambda:[])
    for idx,train_segment in enumerate(unigram_segments):
        sent_id=train_segment.get_parent().id    
        winningHighlight=list(train_marginals[idx])
        cue=train_segment.get_contexts()[0]
        aggregated_sent[sent_id]+=[(cue.char_start,cue.char_end,get_candidate_text(train_segment),winningHighlight)]

        doc_id=train_segment.get_parent().get_parent().name
        if doc_id not in aggregated_doc:
            aggregated_doc[doc_id]=train_segment.get_parent().get_parent().sentences


    df_list=[]      
    print("csv paperID [start, end] as ",list(aggregated_doc.keys())[0],list(aggregated_doc.keys())[-1])
    
    for doc_id in aggregated_doc:
        globalPsn=1
        for sent in aggregated_doc[doc_id]:
            sent_id=sent.id
            if sent_id not in aggregated_sent:
                raise ValueError('we have no info about this sent'+str(sent))
                break
            aggregated_sent[sent_id]=sorted(aggregated_sent[sent_id], key=lambda x: x[0])
            for idx,pair in enumerate(aggregated_sent[sent_id]):
                text=pair[2]
                df_list+=[[pair[3],doc_id,globalPsn,text]]
                globalPsn+=1


    df=pd.DataFrame(df_list,columns=['winningHighlight', 'paperID', 'globalPsn','content'])
    df.to_csv(open(csv_path,"w"))   # in the spreadsheet, punctuations are splitted

# smooth_window=0
# write_csv_gen_label(unigram_segments,train_marginals,"data/annotations_2k/onset_split"+str(train_bucket)+"_window"+str(smooth_window)+".csv")
# for smooth_window in [3,5,7]:
#     write_csv_gen_label(unigram_segments,train_marginals,"data/annotations_2k/split"+str(train_bucket)+"_window"+str(smooth_window)+".csv",smooth_window=smooth_window)

In [10]:
import numpy as np

def get_candidate_text(segment):
    return segment.get_parent().text[segment.get_contexts()[0].char_start:segment.get_contexts()[0].char_end+1]

def write_csv_from_L_train(L_train,csv_path,session):
    
    aggregated_doc=defaultdict(lambda:[])
    aggregated_sent=defaultdict(lambda:[])
    LF_list=purpose_LFs+mechanism_LFs+null_LFs
    
    non_zero_array=L_train.nonzero()

    train_marginals_tmp=np.zeros([L_train.shape[0],3])
    train_marginals_tmp[:,2]=1
    unigram_segments_tmp=[]
    
    for idx in range(L_train.shape[0]):
        unigram_segments_tmp+=[L_train.get_candidate(session,idx)]
    
    print("len(unigram_segments_tmp)==train_marginals.shape[0]?",len(unigram_segments_tmp),train_marginals_tmp.shape[0])
    
    for idx in range(len(non_zero_array[0])):
        row_idx=non_zero_array[0][idx]
        label=L_train[row_idx,non_zero_array[1][idx]]
        train_marginals_tmp[row_idx]=[0,0,0]
        train_marginals_tmp[row_idx][label-1]=1
    
    for idx,train_segment in enumerate(unigram_segments_tmp):
        
        sent_id=train_segment.get_parent().id    
        winningHighlight=list(train_marginals_tmp[idx])
        cue=train_segment.get_contexts()[0]
        aggregated_sent[sent_id]+=[(cue.char_start,cue.char_end,get_candidate_text(train_segment),winningHighlight)]

        doc_id=train_segment.get_parent().get_parent().name
        if doc_id not in aggregated_doc:
            aggregated_doc[doc_id]=train_segment.get_parent().get_parent().sentences

    df_list=[]      
    print("csv paperID [start, end] as ",list(aggregated_doc.keys())[0],list(aggregated_doc.keys())[-1])
    
    for doc_id in aggregated_doc:
        globalPsn=1
        for sent in aggregated_doc[doc_id]:
            sent_id=sent.id
            if sent_id not in aggregated_sent:
                raise ValueError('we have no info about this sent'+str(sent))
                break
            aggregated_sent[sent_id]=sorted(aggregated_sent[sent_id], key=lambda x: x[0])
            for idx,pair in enumerate(aggregated_sent[sent_id]):
                text=pair[2]
                df_list+=[[pair[3],doc_id,globalPsn,text]]
                globalPsn+=1


    df=pd.DataFrame(df_list,columns=['winningHighlight', 'paperID', 'globalPsn','content'])
    df.to_csv(open(csv_path,"w"))   # in the spreadsheet, punctuations are splitted

# smooth_window=0
# write_csv_gen_label(unigram_segments,train_marginals,"data/annotations_2k/onset_split"+str(train_bucket)+"_window"+str(smooth_window)+".csv")
# for smooth_window in [3,5,7]:
#     write_csv_gen_label(unigram_segments,train_marginals,"data/annotations_2k/split"+str(train_bucket)+"_window"+str(smooth_window)+".csv",smooth_window=smooth_window)

In [17]:
smooth_window=0

# write_csv_from_L_train(L_train_tmp,"data/annotations_2k/onset_split"+str(train_bucket)+".csv",session)


# write_csv_gen_label(unigram_segments,train_marginals,"data/annotations_2k/onset_split"+str(train_bucket)+"_window"+str(smooth_window)+".csv")

# purpose_followed_by_goal tested on all unigram_segments from split 8  

for train_bucket in range(36, len(sents_split)):
#     try:
        print("running train_bucket", train_bucket)
#         if train_bucket!=0:
#             %time unigram_segment_extractor.apply(sents_split[train_bucket], split=train_bucket)
        unigram_segments_tmp=session.query(Unigram).filter(Unigram.split == train_bucket).all()
        print("len(train_segments)",len(unigram_segments_tmp))
        print("applying L_train_tmp")
        
#         for segment in unigram_segments_tmp:
#             print(segment)
#             print(get_candidate_text(segment))
#             print(segment.get_parent())

        L_train_tmp=get_L_train(purpose_LFs+mechanism_LFs+null_LFs,split=train_bucket)
        print("creating train_marginals")
        write_csv_from_L_train(L_train_tmp,"data/annotations_2k/onset_split"+str(train_bucket)+"_window"+str(smooth_window)+".csv",session)


#         train_marginals_tmp = gen_model.marginals(L_train_tmp)
#         write_csv_gen_label(unigram_segments_tmp,train_marginals_tmp,"data/annotations_2k/onset_split"+str(train_bucket)+"_window"+str(smooth_window)+".csv")
#     except:
#         continue


running train_bucket 36
len(train_segments) 30768
applying L_train_tmp
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
2018-11-13 22:58:27.782316
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
cids_count 30768
key_group 0
Clearing existing...
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
clearing..
Running UDF...
snorkel_conn_string postgresql:///abstractnet2konset
if snorkel_postgres? True
[========================================] 100%

2018-11-13 23:01:21.421601
<class 'snorkel.annotations.csr_LabelMatrix'>
(30768, 32)


**Total non_overlapping_coverage on L_train (percentage of labelled over all)**  0.01326053042121685

creating train_marginals
len(unigram_segments_tmp)==train_marginals.shape[0]? 30768 30768
csv paperID [start, end] as  semanticDBLP_b7b36b7a7885630c9dcb4b03d86f9efff88f1c22 semanticDBLP_d23b1f704aa817911ee8630063a9d7f6cc0aa92b


In [ ]:
# debug 
smooth_window=0
for train_bucket in range(1,2):# , len(sents_split)):
    print("running train_bucket", train_bucket)
#     if train_bucket!=0:
#         %time unigram_segment_extractor.apply(sents_split[train_bucket], split=train_bucket)
    unigram_segments_tmp=session.query(Unigram).filter(Unigram.split == train_bucket).all()
    print("len(train_segments)",len(unigram_segments_tmp))
#     print("applying L_train_tmp")
    L_train_tmp=get_L_train(purpose_LFs+mechanism_LFs+null_LFs,split=train_bucket)
    print("creating train_marginals")
    train_marginals_tmp = gen_model.marginals(L_train_tmp)
    write_csv_gen_label(unigram_segments_tmp,train_marginals_tmp,"data/annotations_2k/onset_split"+str(train_bucket)+"_window"+str(smooth_window)+".csv")
    

In [26]:
train_marginals_tmp = gen_model.marginals(L_train_tmp)

In [43]:
train_bucket=5
write_csv_gen_label(unigram_segments_tmp,train_marginals_tmp,"data/annotations_2k/onset_split"+str(train_bucket)+"_window"+str(smooth_window)+".csv")

0
10000
20000
30000
40000
csv paperID [start, end] as  2K_dev_1301 2K_dev_1565


In [20]:
count=0
for idx,segment in enumerate(unigram_segments_tmp):
    for lf in purpose_LFs+mechanism_LFs+null_LFs:
        if lf(segment)!=0:
            print(idx,lf.__name__,get_candidate_text(segment),segment.get_parent(),"\n")
            print(L_train_tmp[idx])
            count+=1
    if count>20:
        break
        

28 purpose_we_study we Sentence(Document 2K_dev_1301,1,b'The process we study is the scaled SIS network process, a continuous-time Markov process on a static network.') 

  (0, 5)	1
269 mechanism_we_design we Sentence(Document 2K_dev_1302,4,b'To evaluate the effectiveness of mobile targeting under different social contexts, we designed a randomized field experiment for a large shopping mall in Asia based on 52,500 unique user responses for 252 stores over the course of a 21-day period in April 2015.') 

  (0, 19)	2
300 purpose_to_verb To Sentence(Document 2K_dev_1302,4,b'To evaluate the effectiveness of mobile targeting under different social contexts, we designed a randomized field experiment for a large shopping mall in Asia based on 52,500 unique user responses for 252 stores over the course of a 21-day period in April 2015.') 

  (0, 1)	1
565 purpose_to_verb to Sentence(Document 2K_dev_1303,2,b'We perform spectral analysis on these graph signals, for which it is necessary to addres

In [22]:
pair_list=list(zip(unigram_segments_tmp,train_marginals_tmp))
new_unigram_segments=[]
new_train_marginals=[]
doc_dict=defaultdict(lambda:[])
for ind,pair in enumerate(pair_list):
    if ind%10000==0:
        print(ind)
    docid=pair[0].get_parent().get_parent().name
    doc_dict[docid]+=[pair]

for docid in doc_dict:
    doc_dict[docid]=sorted(doc_dict[docid], key=lambda pair: (pair[0].get_parent().position, pair[0].get_contexts()[0].get_word_start()))

for docid in doc_dict:
    for pair in doc_dict[docid]:
        print(pair[0],pair[1])


0
10000
20000
30000
40000
50000
Unigram(Span("b'Objective'", sentence=750851, chars=[0,8], words=[0,0])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'.'", sentence=750851, chars=[9,9], words=[1,1])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'A'", sentence=750852, chars=[0,0], words=[0,0])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'traditional'", sentence=750852, chars=[2,12], words=[1,1])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'goal'", sentence=750852, chars=[14,17], words=[2,2])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'of'", sentence=750852, chars=[19,20], words=[3,3])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'neural'", sentence=750852, chars=[22,27], words=[4,4])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'recording'", sentence=750852, chars=[29,37], words=[5,5])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'with'", sentence=750852, chars=[39,42], words=[6,6])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'ext

Unigram(Span("b'('", sentence=750877, chars=[87,87], words=[11,11])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'CSMA'", sentence=750877, chars=[89,92], words=[12,12])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b')'", sentence=750877, chars=[94,94], words=[13,13])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'to'", sentence=750877, chars=[96,97], words=[14,14])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'solve'", sentence=750877, chars=[99,103], words=[15,15])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'the'", sentence=750877, chars=[105,107], words=[16,16])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'four'", sentence=750877, chars=[109,112], words=[17,17])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'problems'", sentence=750877, chars=[114,121], words=[18,18])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'mentioned'", sentence=750877, chars=[123,131], words=[19,19])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'above'", se

Unigram(Span("b'induced'", sentence=750890, chars=[147,153], words=[21,21])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'by'", sentence=750890, chars=[155,156], words=[22,22])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'choice'", sentence=750890, chars=[158,163], words=[23,23])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'framing'", sentence=750890, chars=[165,171], words=[24,24])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'.'", sentence=750890, chars=[172,172], words=[25,25])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'Implications'", sentence=750891, chars=[0,11], words=[0,0])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'for'", sentence=750891, chars=[13,15], words=[1,1])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'privacy'", sentence=750891, chars=[17,23], words=[2,2])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'decision'", sentence=750891, chars=[25,32], words=[3,3])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'res

Unigram(Span("b'more'", sentence=750910, chars=[33,36], words=[7,7])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'street'", sentence=750910, chars=[38,43], words=[8,8])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'closure'", sentence=750910, chars=[45,51], words=[9,9])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'nearby'", sentence=750910, chars=[53,58], words=[10,10])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'leads'", sentence=750910, chars=[60,64], words=[11,11])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'to'", sentence=750910, chars=[66,67], words=[12,12])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'a'", sentence=750910, chars=[69,69], words=[13,13])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'4.7'", sentence=750910, chars=[71,73], words=[14,14])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'%'", sentence=750910, chars=[75,75], words=[15,15])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'decrease'", sentence=750910,

Unigram(Span("b'because'", sentence=750924, chars=[67,73], words=[9,9])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'it'", sentence=750924, chars=[75,76], words=[10,10])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'involves'", sentence=750924, chars=[78,85], words=[11,11])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'solving'", sentence=750924, chars=[87,93], words=[12,12])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'an'", sentence=750924, chars=[95,96], words=[13,13])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'optimization'", sentence=750924, chars=[98,109], words=[14,14])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'problem'", sentence=750924, chars=[111,117], words=[15,15])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'with'", sentence=750924, chars=[119,122], words=[16,16])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'non'", sentence=750924, chars=[124,126], words=[17,17])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'

...

Unigram(Span("b'scheduling'", sentence=750794, chars=[236,245], words=[41,41])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'cycle'", sentence=750794, chars=[247,251], words=[42,42])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'.'", sentence=750794, chars=[252,252], words=[43,43])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'TetriSched'", sentence=750794, chars=[254,263], words=[44,44])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'leverages'", sentence=750794, chars=[265,273], words=[45,45])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'information'", sentence=750794, chars=[275,285], words=[46,46])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'supplied'", sentence=750794, chars=[287,294], words=[47,47])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'by'", sentence=750794, chars=[296,297], words=[48,48])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'the'", sentence=750794, chars=[299,301], words=[49,49])) [0.33333333 0.33333333 0.333333

Unigram(Span("b'By'", sentence=750802, chars=[0,1], words=[0,0])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'improving'", sentence=750802, chars=[3,11], words=[1,1])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'ML'", sentence=750802, chars=[13,14], words=[2,2])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'progress'", sentence=750802, chars=[16,23], words=[3,3])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'per'", sentence=750802, chars=[25,27], words=[4,4])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'iteration'", sentence=750802, chars=[29,37], words=[5,5])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'through'", sentence=750802, chars=[39,45], words=[6,6])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'SchMP'", sentence=750802, chars=[47,51], words=[7,7])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'programming'", sentence=750802, chars=[53,63], words=[8,8])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'whilst'", sentence=750

Unigram(Span("b'youth'", sentence=750819, chars=[86,90], words=[15,15])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'violence'", sentence=750819, chars=[92,99], words=[16,16])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'perpetrated'", sentence=750819, chars=[101,111], words=[17,17])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'by'", sentence=750819, chars=[113,114], words=[18,18])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'groups'", sentence=750819, chars=[116,121], words=[19,19])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'and'", sentence=750819, chars=[123,125], words=[20,20])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'individuals'", sentence=750819, chars=[127,137], words=[21,21])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b','", sentence=750819, chars=[138,138], words=[22,22])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'recognizing'", sentence=750819, chars=[140,150], words=[23,23])) [0.33333333 0.33333333 0.33333333]
U

Unigram(Span("b'integrate'", sentence=750830, chars=[29,37], words=[6,6])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'diverse'", sentence=750830, chars=[39,45], words=[7,7])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'streams'", sentence=750830, chars=[47,53], words=[8,8])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'of'", sentence=750830, chars=[55,56], words=[9,9])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'IS'", sentence=750830, chars=[58,59], words=[10,10])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'literature'", sentence=750830, chars=[61,70], words=[11,11])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'on'", sentence=750830, chars=[72,73], words=[12,12])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'privacy'", sentence=750830, chars=[75,81], words=[13,13])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'decision'", sentence=750830, chars=[83,90], words=[14,14])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'making'", s

Unigram(Span("b'graph'", sentence=750847, chars=[82,86], words=[12,12])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'data'", sentence=750847, chars=[88,91], words=[13,13])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b','", sentence=750847, chars=[92,92], words=[14,14])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'and'", sentence=750847, chars=[94,96], words=[15,15])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'recently'", sentence=750847, chars=[98,105], words=[16,16])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b','", sentence=750847, chars=[106,106], words=[17,17])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'the'", sentence=750847, chars=[108,110], words=[18,18])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'tensors'", sentence=750847, chars=[112,118], words=[19,19])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'of'", sentence=750847, chars=[120,121], words=[20,20])) [0.33333333 0.33333333 0.33333333]
Unigram(Span("b'multimodal'", 

In [61]:
# You're trying to build one large dataframe out of the rows of many dataframes who all have the same column names. axis should be 0 (the default), not 1. Also you don't need to specify a type of join. This will have no effect since the column names are the same for each dataframe.

# df = pd.concat([df1, df2, df3])

sub_dfs=[]
for train_bucket in range(len(sents_split)):
    sub_dfs+=[pd.read_csv(open("data/annotations_2k/split"+str(train_bucket)+".csv","r"))]
df = pd.concat(sub_dfs)
df=df.drop(columns=['Unnamed: 0'])
df.to_csv(open("data/annotations_2k/joint_split.csv","w"))

In [62]:
df2=df.copy()
import ast
import numpy as np

def transform_gm_label(x):
    x=ast.literal_eval(x)
    if abs(x[0]-x[1])<1e-4 and abs(x[1]-x[2])<1e-4:
        return [0,0,1]
    elif np.argmax(x)==0:
        return [1,0,0]
    return [0,1,0]

df2['winningHighlight'] = df2['winningHighlight'].apply(lambda x: transform_gm_label(x))
df2.to_csv(open("data/annotations_2k/joint_split_hard_as_soft.csv","w"))

In [65]:
import ast
import numpy as np

def transform_gm_label(x,threshold=0.33):
    x=ast.literal_eval(x)
    if abs(x[0]-x[1])<1e-4 and abs(x[1]-x[2])<1e-4:
        return [0,0,0]
    elif np.argmax(x)==0 and x[0]>threshold:
        return [1,0,0]
    elif np.argmax(x)==1 and x[1]>threshold:
        return [0,1,0]
    elif np.argmax(x)==2 and x[2]>threshold:
        return [0,0,1]
    else:
        return [0,0,0]

for threshold in [0.33, 0.4, 0.5, 0.6, 0.7, 0.75, 0.8, 0.85, 0.9, 0.95]:
    df2=df.copy()   
    df2['winningHighlight'] = df2['winningHighlight'].apply(lambda x: transform_gm_label(x,threshold=threshold))
    df2.to_csv(open("data/annotations_2k/joint_split_hard_as_soft_break_tie_"+str(threshold)+".csv","w"))
    

### Peripheral codes to examine Candidates

In [48]:
# TODO get_surrounding_words maybe group segments back to doc level from  Sentence has words in its __dict__ 

# visualize purpose probability


# pair_list=list(zip(unigram_segments,list(train_marginals[:,0].reshape(-1))))


# Find a test case span!!!
count=0
for idx,segment in enumerate(unigram_segments):
    if "indicates that" in segment.get_parent().__dict__['words']:
        print(idx,segment.get_parent().__dict__['text'])
        if count>30:
            break
        count+=1
    
# input()
purpose_LFs=[]
from LF.util_common_default_categorical_1022 import purpose_LFs,mechanism_LFs

for i in range(695,725):
    print(unigram_segments[i])
    print(unigram_segments[i].get_parent().__dict__['text'])
    print(purpose_LFs[-1](unigram_segments[i]))
#     print(purpose_LFs[-1].__name__)
    print()
    
    
# print(unigram_segments[165],)

segment=unigram_segments[165]
# print((segment.get_contexts()[0].__dict__))
docid=segment.get_parent().get_parent().name
print(segment)
print("sent __dict__",segment.get_parent().__dict__)
print("sent pos in doc??", segment.get_parent().position)
# print("sent pos in doc??", segment.get_parent().get_parent().sentences.index(segment.get_parent()))

print(docid)

# print(segment.get_parent().get_parent().__dict__)
print(segment.get_parent().text[segment.unigram_cue.char_start:segment.unigram_cue.char_end+1])

unigram_psn=segment.unigram_cue.get_word_start()
print("unigram position?? ",unigram_psn)#.__dict__['words'])

its_pos_tag=segment.get_parent().__dict__['pos_tags'][unigram_psn]
print("its_pos_tag",its_pos_tag,"\n")

# its_surrounding_pos_tag=get_sourrounding_pos_tag(segment,3)
# print("unigram pos tag",get_sourrounding_pos_tag(segment,1))
# print("trigram pos tag",get_sourrounding_pos_tag(segment,3))
# print("5gram pos tag",get_sourrounding_pos_tag(segment,5))


Unigram(Span("b'tend'", sentence=2248, chars=[39,42], words=[9,9]))
Specifically, we showed that (a) users tend to like stories submitted by friends and (b) users tend to like stories their friends read and liked.
0

Unigram(Span("b'like'", sentence=2248, chars=[103,106], words=[23,23]))
Specifically, we showed that (a) users tend to like stories submitted by friends and (b) users tend to like stories their friends read and liked.
0

Unigram(Span("b'to'", sentence=2248, chars=[44,45], words=[10,10]))
Specifically, we showed that (a) users tend to like stories submitted by friends and (b) users tend to like stories their friends read and liked.
0

Unigram(Span("b'stories'", sentence=2248, chars=[108,114], words=[24,24]))
Specifically, we showed that (a) users tend to like stories submitted by friends and (b) users tend to like stories their friends read and liked.
0

Unigram(Span("b'like'", sentence=2248, chars=[47,50], words=[11,11]))
Specifically, we showed that (a) users tend to like

### Related stackoverflow questions
https://datascience.stackexchange.com/questions/20071/how-do-i-load-fasttext-pretrained-model-with-gensim?noredirect=1


To test the effectivenss of fasttext WE:
1. we will examine the similarity between developed and develop
2. propose and proposed
3. introduce and propose
4. approach and method
5. approach and model
6. algorithm and model
7. algorithm and theory
5. datasets and benchmark 
6. dataset and corpus
7. explosive and emerging
8. emerging and arising
9. growth and development

In [ ]:
import gensim
import os
from gensim.models.word2vec import LineSentence
from gensim.models.fasttext import FastText as FT_gensim

model_wrapper.save('saved_model_wrapper')
loaded_model = FT_wrapper.load('saved_model_wrapper')
print(loaded_model)

print('night' in model_wrapper.wv.vocab)
print('nights' in model_wrapper.wv.vocab)
print(model_wrapper['night'])
print(model_wrapper['nights'])


from gensim.models.wrappers import FastText

model = FastText.load_fasttext_format('wiki.simple')

print(model.most_similar('teacher'))
# Output = [('headteacher', 0.8075869083404541), ('schoolteacher', 0.7955552339553833), ('teachers', 0.733420729637146), ('teaches', 0.6839243173599243), ('meacher', 0.6825737357139587), ('teach', 0.6285147070884705), ('taught', 0.6244685649871826), ('teaching', 0.6199781894683838), ('schoolmaster', 0.6037642955780029), ('lessons', 0.5812176465988159)]

print(model.similarity('teacher', 'teaches'))
# Output = 0.683924396754


